# Using rapidfuzz to extract affiliatuons from RES

First the JSON output file from tezseract is read in and made into a useable dataframe

In [1]:
#Importing the libraries
import json
import pandas as pd
from rapidfuzz import process
import requests

# Load input files from github
#tesseract_input = requests.get('https://raw.githubusercontent.com/Matt970204/Affiliations_V2/main/1_Input%20files%20and%20processing%20input%20files/1_1_Input%20files/Tesseract%20affiliation%20output/AER/AER_aff_output_1971_2010.json')
#json_data = tesseract_input.json()

# Import JSON file
f = open('/Users/MattJohnson/Desktop/Affiliations/1_Input files and processing input files/1_1_Input files/Tesseract affiliation output/JPE/JPE_affiliation_output_1940_2010.json')
json_data = json.load(f)

# Define Journal and Dataframe
Journal_Name = 'JPE'
Reference_Data_List = []

# Extract Json Data into dataframe
for key1, value1 in json_data.items():
    Article_ID = key1
    content_type = value1["content_type"]
    author_list = value1["authors"]
    authorsNo = len(author_list)
    stable_url = value1["stable_url"]
    for key2 in value1["affiliations"]:
        Ref_type = key2
        if key2 == "found":
            ref_string = value1["affiliations"][key2]
        else: 
            for key3 in value1["affiliations"]["raw"]:
                if len(value1["affiliations"]["raw"]) > 1:
                    print(key1, "   ",len(value1["affiliations"]["raw"]))
                if key3 == "1":
                    print(key3)
                    ref_string = value1["affiliations"][key2][key3]
                    print(ref_string)

    Reference_Data_List.append({'Journal_Name' : Journal_Name,
    'Authors_count' : authorsNo, 
    'Authors_list' : author_list,
    'Article_ID' : Article_ID, 'content_type' : content_type,
    'stable_url' : stable_url, 
    'Ref_type': Ref_type,  'ref_string':ref_string })


JPE_aff_ref_output_1940_2010 = pd.DataFrame.from_records(Reference_Data_List)     
JPE_aff_ref_output_1940_2010.to_excel('/Users/MattJohnson/Desktop/Affiliations/2_Extracting affilitations/2_Fuzzy matching/Working files/JPE_aff_ref_output_1940_2010.xlsx')        

1
['Preface\n', 'The papers in this issue of the /PE were presented at a Festschrift con-\nference in honor of James J. Heckman\'s 65th birthday. The conference\nattendees included many of his former graduate students, coauthors,\nand colleagues. Thirteen excellent papers were submitted to this special\nissue. They went through the regular refereeing process, and six were\nultimately accepted. Below, we describe how the papers included in this\nissue were inspired and influenced by Heckman\'s research.\n\nHeckman has produced a large body of research examining the ori-\ngins of inequality in socioeconomic outcomes. An important insight\nfrom this research is that the family has a large influence on an individ-\nual\'s human capital formation. This finding led Heckman to state that\n*the accident of birth is a major source of inequality" (2008, 289).! After\nHeckman won the Nobel Prize in 2000, a large part of his research focused\non understanding what types of policy interventions can

Next the Unique list of universities is read in, this is used as a database to check the affiliton string against using rapidfuzz. 

In [2]:
# Load in the list of unique Universites from github stored in 2_fuzzy matching
#affs = pd.read_excel("https://raw.githubusercontent.com/Matt970204/Affiliations_V2/main/2_Extracting%20affilitations/2_Fuzzy%20matching/University%20list/Unique%20Universities.xlsx")


affs = pd.read_excel('/Users/MattJohnson/Desktop/Affiliations/2_Extracting affilitations/2_Fuzzy matching/University list/Unique Universities.xlsx')
print(affs.shape)

for i in range(len(affs)):
    #Replaceing title case and stripping leading space
    #affs.iat[i,0] = affs.iat[i,0].strip().title()
    affs.iloc[i]['Affilliation'] = affs.iloc[i]['Affilliation'].strip().title()
    #affs.iat[i,0] = affs.iat[i,0].strip().upper()

Affiliation_choices = affs['Affilliation'].values.tolist()

print(affs['Affilliation'].head())

(850, 14)


/var/folders/23/ft9qf9c11rj_vqhbjml910f40000gn/T/ipykernel_5443/1542333116.py:11: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  affs.iloc[i]['Affilliation'] = affs.iloc[i]['Affilliation'].strip().title()


0      Yale University
1            Cambridge
2              Harvard
3               Oxford
4    Oxford University
Name: Affilliation, dtype: object


In [3]:
#testdata = RES_1940_2010.loc[0:20].reset_index(drop = True)
testdata = JPE_aff_ref_output_1940_2010

for i in range(len(testdata)):
    if testdata.iloc[i]['Ref_type'] == "raw":
        testdata.loc[i,['ref_string_clean1']] =  " ".join(testdata.iloc[i]['ref_string'])
        #x = " ".join(testdata.iloc[i]['ref_string'])
        #print(x)
        testdata.loc[i,['ref_string_clean1']] = testdata.iloc[i]['ref_string_clean1'].strip().title()
    else:
        testdata.loc[i,['ref_string_clean1']] = testdata.iloc[i]['ref_string'].strip().title()

print(testdata.columns.values)

['Journal_Name' 'Authors_count' 'Authors_list' 'Article_ID' 'content_type'
 'stable_url' 'Ref_type' 'ref_string' 'ref_string_clean1']


In [4]:
#Reading in the master file and correctly formatting the article ID to match back onto the meltef file

#Load in master from Github
#AER_master = pd.read_excel("https://raw.githubusercontent.com/Matt970204/Affiliations_V2/main/1_Input%20files%20and%20processing%20input%20files/1_1_Input%20files/Master%20lists/Processed/AER_processed.xlsx")

#Local store of AER_master
JPE_master = pd.read_excel('/Users/MattJohnson/Desktop/Affiliations/1_Input files and processing input files/1_1_Input files/Master lists/Processed/JPE_processed.xlsx')
for i in range(len(JPE_master)):
    JPE_master.loc[i,['Article_ID']] = JPE_master.loc[i,['stable_url']].to_string().rsplit('/',1)[-1]

JPE_master_condenced  = JPE_master[['Article_ID','year']]
JPE_master_condenced['year'] = JPE_master_condenced['year'].astype('int')
JPE_master_condenced.head()

/var/folders/23/ft9qf9c11rj_vqhbjml910f40000gn/T/ipykernel_5443/679620167.py:12: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  JPE_master_condenced['year'] = JPE_master_condenced['year'].astype('int')


Article_ID  year
0   26549909  2016
1   26549910  2016
2   26549911  2016
3   26549912  2016
4   26549913  2016

In [5]:
# MErging the msterfile onto the new melted file to get additional data
testdata_merged = testdata.merge(JPE_master_condenced, how = 'left', on = 'Article_ID')
testdata_merged = testdata_merged.sort_values(by=['year'])
testdata = testdata_merged.reset_index(drop = True)

In [6]:
# Excel output to get an overview of the data
testdata.head
testdata.to_excel('/Users/MattJohnson/Desktop/Affiliations/2_Extracting affilitations/2_Fuzzy matching/JPE/Test files/JPE_aff_ref_output_1940_2010_affs_out setup.xlsx') 

In [7]:
list(testdata.columns.values)

['Journal_Name',
 'Authors_count',
 'Authors_list',
 'Article_ID',
 'content_type',
 'stable_url',
 'Ref_type',
 'ref_string',
 'ref_string_clean1',
 'year']

In [17]:
import re
from rapidfuzz import fuzz
import math


#x = 2233

for x in range(len(testdata)):
#for x in range(3627,3628):
#80,114
    authors = testdata.iloc[x]['Authors_list']
    str1 = testdata.iloc[x]['ref_string_clean1']

#Splitting up the string into authors lines
    ref_split = re.split(r"\n",str1 )
    while("" in ref_split):
        ref_split.remove("")
    #print(ref_split)
    print(ref_split)

#Finding the authors name and corrosponding affiliations
    count_found = 0
    #Loop through auhor names in author list
    for d in range(len(authors)):
        #Loop through the data that is split into possible authors affiliations
        for j in range(len(ref_split)):
            #Check if the author name is in the split string
            ratio_author  = fuzz.partial_ratio(ref_split[j], authors[d])
            #print(ratio,x)
            if ratio_author > 93:
                count_found = count_found +1
                #print(count_found)

                #append the next line to a column for each author
                # This will ensure each author is accounted for
                if j+1 < len(ref_split):
                    #print(ratio_author)
                    #print(ref_split[j+1], authors[d])
                    testdata.loc[x, str(d)+'_author'] = authors[d]

                    # checking for short erroenous splits
                    if len(ref_split[j+1]) > 3:
                        testdata.loc[x, str(d)+'_author_affs'] = ref_split[j+1]
                    else:
                        testdata.loc[x, str(d)+'_author_affs'] = ''
                    #print(testdata.loc[x, str(d)+'_author_affs'])

            # Prevents double finding of author name, sometimes name occurs twice 
            # but first occurance is the affiliation
            if count_found == len(authors):
                break
                #else:

# Finding the affiliations per author
    #for i in range(0,1):
    #Loop through authors
    for i in range(len(authors)):      
        # Create new affiliations list for each author
        affiliations = []
        #Create the variable or where the authors affilaiton is stored
        item = str(str(i)+'_author_affs')
        #print(item)
        #print(testdata.iloc[x][item])
        # Fuzzy matching loop for possible affiliations

        #Get the affiliation associated with each author
        author_aff = testdata.iloc[x][item]
        print(author_aff)
        if author_aff not in('University Of Texas','University Of California','University','Universi'):
            for z in Affiliation_choices:
                #print(item)
                #print(testdata.iloc[x][item])
                if pd.notnull(author_aff):
                    #print(author_aff)
                    # z is the affilition choice being matched
                    # author_aff is the input string based on authors
                        ratio  = fuzz.partial_ratio(author_aff, z)
                        if ratio > 94:
                            #print(z)
                            #print(item)
                            #print(ratio , x)
                            #print(testdata.iloc[x][str(i)+'_author_affs'])
                            #Appending the affiliation and the ratio to affiliations list
                            affiliations.append([z,ratio])
                                    #Errors
                            if len(affiliations) == 8:
                                break
        elif author_aff == 'University Of Texas':
            affiliations.append(['University Of Texas',100])
        elif author_aff == 'University Of California':
            affiliations.append(['University Of Texas',100])
    
        #Append full affiliations list
        #print(affiliations)
        #testdata.loc[x, '0_affiliations_list'] = affiliations

        #Add each aff to a new column for each author
        for e in range(len(affiliations)):
            testdata.loc[x,str(i)+'_'+ str(e)+'_Auth_aff'] = affiliations[e][0]
            testdata.loc[x,str(i)+'_'+ str(e)+'_Auth_aff_ratio'] = affiliations[e][1]
            print(affiliations[e][0])
            print(affiliations[e][1])
            #print(testdata.loc[x,'Auth_'+str(i)+'_'+ str(e)+'_aff'])
    print(x)
    

['Comments On W. I. King: "Are We Suffering', 'From Economic Maturity?":', 'Gerhard Colm', 'Washington, D.C.', 'From Economic Maturity?" Is Very Useful Because It Helps To', 'Clarify The Issues Which Are Involved In This Problem. In These', 'Comments I Cannot Undertake To Give An Answer To The Question Myself,', 'But I Shall Try To Indicate Where, To My Mind, The Real Problems Of A', 'Maturing Economy Lie.', 'Mr. King Presents His Case Very Nicely In The Form Of An Analogy.', "The Superintendent Of George Washington'S Estate Is Alarmed By The", 'Fact That All Work For Clearing The Land, For Building The House, The', 'Barns, The Grist Mill, The Roads, And The Bridges, Has Been Done. What', 'Shall He Do With The Slaves Now? Are They Condemned To Permanent', 'Unemployment, Asks The Superintendent Anxiously. But George Wash-', 'Ington Cheers Him Up. He Is Happy That Now More Comfortable Quarters', 'For The Slaves Can Be Built; That Luxurious Furniture For Mrs. Washing-', 'Ton Can Be Constr

/var/folders/23/ft9qf9c11rj_vqhbjml910f40000gn/T/ipykernel_5443/523173047.py:100: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  testdata.loc[x,str(i)+'_'+ str(e)+'_Auth_aff_ratio'] = affiliations[e][1]
/var/folders/23/ft9qf9c11rj_vqhbjml910f40000gn/T/ipykernel_5443/523173047.py:100: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  testdata.loc[x,str(i)+'_'+ str(e)+'_Auth_aff_ratio'] = affiliations[e][1]
/var/folders/23/ft9qf9c11rj_vqhbjml910f40000gn/T/ipykernel_5443/523173047.py:100: SettingWithCopyWarning: 
A

48
['Prices Under Monopoly And Competition:', 'T. De Scitovszky', 'New York City', 'T Is A Common Belief Among Economists That Prices Are More', 'Stable Under Monopoly Than Under Competition. The Rigidity', 'Of The Price And Cost Structure Of Our Economic System Is', 'Often Blamed For Our Economic Evils, And Trade-Unionism And Mo-', 'Nopoly Are Mainly Held Responsible For It. A Random Perusal Of', 'The Very Extensive Literature On The Problem Of Price Rigidity Will', 'Convince The Reader Of The Generality Of This Belief; At The Same', 'Time I Know Of No Theoretical Proof Or Argument On Which It', 'Might Be Based.* In The American Literature Statistical Evidence', 'Is Cited As Proof; But This Is Of Doubtful Validity, As I Hope To', 'Show Below.', 'The Belief That Prices Are More Flexible Under Competition Than', 'Under Monopoly Has Probably Sprung From The Fact That Competi-', "Tive Producers Tend To Undercut One Another'S Price In Response", 'To Flagging Demand Or Falling Costs, While 

In [13]:
author_aff = 'University Of Texas'
if author_aff not in('University Of Texas','University Of California'):
  print("F")
elif author_aff == 'University Of Texas':
  print("Tex")
elif author_aff == 'University Of California':
  print("Cal")

Tex


In [18]:
print(testdata.columns.values)

['Journal_Name' 'Authors_count' 'Authors_list' 'Article_ID' 'content_type'
 'stable_url' 'Ref_type' 'ref_string' 'ref_string_clean1' 'year'
 '0_author' '0_author_affs' '0_0_Auth_aff' '0_1_Auth_aff' '0_2_Auth_aff'
 '0_3_Auth_aff' '0_4_Auth_aff' '0_5_Auth_aff' '1_author' '1_author_affs'
 '1_0_Auth_aff' '1_1_Auth_aff' '1_2_Auth_aff' '1_3_Auth_aff'
 '1_4_Auth_aff' '2_author' '2_author_affs' '2_0_Auth_aff' '2_1_Auth_aff'
 '2_2_Auth_aff' '2_3_Auth_aff' '2_4_Auth_aff' '3_author' '3_author_affs'
 '3_0_Auth_aff' '3_1_Auth_aff' '3_2_Auth_aff' '4_author' '4_author_affs'
 '4_0_Auth_aff' '4_1_Auth_aff' '5_author' '5_author_affs' '5_0_Auth_aff'
 '5_1_Auth_aff' '0_0_Auth_aff_ratio' '0_1_Auth_aff_ratio'
 '1_0_Auth_aff_ratio' '1_1_Auth_aff_ratio' '0_2_Auth_aff_ratio'
 '0_3_Auth_aff_ratio' '2_0_Auth_aff_ratio' '3_0_Auth_aff_ratio'
 '2_1_Auth_aff_ratio' '0_4_Auth_aff_ratio' '0_5_Auth_aff_ratio'
 '0_6_Auth_aff' '0_6_Auth_aff_ratio' '0_7_Auth_aff' '0_7_Auth_aff_ratio'
 '1_2_Auth_aff_ratio' '1_3_Auth_aff_ra

In [15]:
#testdata = testdata[['Journal_Name' ,'Authors_count', 'Authors_list', 'Article_ID', 'content_type',
# 'stable_url', 'Ref_type' ,'ref_string', 'ref_string_clean1', 'year',
#'0_author', '0_author_affs', '0_0_Auth_aff', '0_1_Auth_aff', '0_2_Auth_aff', '0_3_Auth_aff', '0_4_Auth_aff', '0_5_Auth_aff',
# # '0_6_Auth_aff', '0_7_Auth_aff',
# '1_author', '1_author_affs', '1_0_Auth_aff', '1_1_Auth_aff', '1_2_Auth_aff', '1_3_Auth_aff','1_4_Auth_aff',
# #'1_5_Auth_aff', '1_6_Auth_aff', '1_7_Auth_aff',
# '2_author', '2_author_affs', '2_0_Auth_aff', '2_1_Auth_aff', '2_2_Auth_aff', '2_3_Auth_aff', '2_4_Auth_aff',
# '3_author', '3_author_affs' , '3_0_Auth_aff' ,'3_1_Auth_aff', '3_2_Auth_aff',
# '4_author', '4_author_affs', '4_0_Auth_aff', '4_1_Auth_aff',
# '5_author', '5_author_affs', '5_0_Auth_aff', '5_1_Auth_aff']]

In [21]:
testdata = testdata[['Journal_Name' ,'Authors_count', 'Authors_list', 'Article_ID', 'content_type',
 'stable_url', 'Ref_type' ,'ref_string', 'ref_string_clean1', 'year',
 '0_author', '0_author_affs', 
 '0_0_Auth_aff', '0_0_Auth_aff_ratio',
 '0_1_Auth_aff', '0_1_Auth_aff_ratio',
 '0_2_Auth_aff', '0_2_Auth_aff_ratio',
 '0_3_Auth_aff', '0_3_Auth_aff_ratio',
 '0_4_Auth_aff', '0_4_Auth_aff_ratio' ,
 '0_5_Auth_aff','0_5_Auth_aff_ratio',
 '1_author', '1_author_affs', 
 '1_0_Auth_aff', '1_0_Auth_aff_ratio',
 '1_1_Auth_aff', '1_1_Auth_aff_ratio',
 '1_2_Auth_aff', '1_2_Auth_aff_ratio',
 '1_3_Auth_aff', '1_3_Auth_aff_ratio',
 '1_4_Auth_aff','1_4_Auth_aff_ratio',
 #'1_5_Auth_aff', '1_6_Auth_aff', '1_7_Auth_aff',
 '2_author', '2_author_affs', '2_0_Auth_aff', '2_1_Auth_aff', '2_2_Auth_aff', '2_3_Auth_aff', '2_4_Auth_aff',
 '3_author', '3_author_affs' , '3_0_Auth_aff' ,'3_1_Auth_aff', '3_2_Auth_aff',
 '4_author', '4_author_affs', '4_0_Auth_aff', '4_1_Auth_aff',
 '5_author', '5_author_affs', '5_0_Auth_aff', '5_1_Auth_aff']]

In [22]:
# Excel output to get an overview of the data
testdata.head
testdata.to_excel('/Users/MattJohnson/Desktop/Affiliations/2_Extracting affilitations/2_Fuzzy matching/JPE/Test files/JPE_aff_ref_output_1940_2010_affs_out authors.xlsx') 

In [61]:
author_aff = "Univensity of Catifornia, Berkeley , Privceton University and Unitersity Of Chicago"
for z in Affiliation_choices:
        ratio  = fuzz.partial_ratio(author_aff, z)
        if ratio >= 94:
                print("Input:",author_aff)
                print("Output:",z)
                print("Ratio:",ratio)

Input: Univensity of Catifornia, Berkeley , Privceton University and Unitersity Of Chicago
Output: Princeton University
Ratio: 95.0
Input: Univensity of Catifornia, Berkeley , Privceton University and Unitersity Of Chicago
Output: University Of Chicago
Ratio: 95.23809523809523
Input: Univensity of Catifornia, Berkeley , Privceton University and Unitersity Of Chicago
Output: University of California, Berkeley
Ratio: 94.11764705882352


In [ ]:
help(fuzz.partial_ratio)

Help on cython_function_or_method in module rapidfuzz.fuzz_cpp:

partial_ratio(s1, s2, *, processor=None, score_cutoff=None)
    Searches for the optimal alignment of the shorter string in the
    longer string and returns the fuzz.ratio for this alignment.
    
    Parameters
    ----------
    s1 : Sequence[Hashable]
        First string to compare.
    s2 : Sequence[Hashable]
        Second string to compare.
    processor: callable, optional
        Optional callable that is used to preprocess the strings before
        comparing them. Default is None, which deactivates this behaviour.
    score_cutoff : float, optional
        Optional argument for a score threshold as a float between 0 and 100.
        For ratio < score_cutoff 0 is returned instead. Default is 0,
        which deactivates this behaviour.
    
    Returns
    -------
    similarity : float
        similarity between s1 and s2 as a float between 0 and 100
    
    Notes
    -----
    Depending on the length of the 